# Starbucks Capstone Challenge

### Introduction

This data set contains simulated data that mimics customer behavior on the Starbucks rewards mobile app. Once every few days, Starbucks sends out an offer to users of the mobile app. An offer can be merely an advertisement for a drink or an actual offer such as a discount or BOGO (buy one get one free). Some users might not receive any offer during certain weeks. 

Not all users receive the same offer, and that is the challenge to solve with this data set.

Your task is to combine transaction, demographic and offer data to determine which demographic groups respond best to which offer type. This data set is a simplified version of the real Starbucks app because the underlying simulator only has one product whereas Starbucks actually sells dozens of products.

Every offer has a validity period before the offer expires. As an example, a BOGO offer might be valid for only 5 days. You'll see in the data set that informational offers have a validity period even though these ads are merely providing information about a product; for example, if an informational offer has 7 days of validity, you can assume the customer is feeling the influence of the offer for 7 days after receiving the advertisement.

You'll be given transactional data showing user purchases made on the app including the timestamp of purchase and the amount of money spent on a purchase. This transactional data also has a record for each offer that a user receives as well as a record for when a user actually views the offer. There are also records for when a user completes an offer. 

Keep in mind as well that someone using the app might make a purchase through the app without having received an offer or seen an offer.

### Example

To give an example, a user could receive a discount offer buy 10 dollars get 2 off on Monday. The offer is valid for 10 days from receipt. If the customer accumulates at least 10 dollars in purchases during the validity period, the customer completes the offer.

However, there are a few things to watch out for in this data set. Customers do not opt into the offers that they receive; in other words, a user can receive an offer, never actually view the offer, and still complete the offer. For example, a user might receive the "buy 10 dollars get 2 dollars off offer", but the user never opens the offer during the 10 day validity period. The customer spends 15 dollars during those ten days. There will be an offer completion record in the data set; however, the customer was not influenced by the offer because the customer never viewed the offer.

### Cleaning

This makes data cleaning especially important and tricky.

You'll also want to take into account that some demographic groups will make purchases even if they don't receive an offer. From a business perspective, if a customer is going to make a 10 dollar purchase without an offer anyway, you wouldn't want to send a buy 10 dollars get 2 dollars off offer. You'll want to try to assess what a certain demographic group will buy when not receiving any offers.

### Final Advice

Because this is a capstone project, you are free to analyze the data any way you see fit. For example, you could build a machine learning model that predicts how much someone will spend based on demographics and offer type. Or you could build a model that predicts whether or not someone will respond to an offer. Or, you don't need to build a machine learning model at all. You could develop a set of heuristics that determine what offer you should send to each customer (i.e., 75 percent of women customers who were 35 years old responded to offer A vs 40 percent from the same demographic to offer B, so send offer A).

# Data Sets

The data is contained in three files:

* portfolio.json - containing offer ids and meta data about each offer (duration, type, etc.)
* profile.json - demographic data for each customer
* transcript.json - records for transactions, offers received, offers viewed, and offers completed

Here is the schema and explanation of each variable in the files:

**portfolio.json**
* id (string) - offer id
* offer_type (string) - type of offer ie BOGO, discount, informational
* difficulty (int) - minimum required spend to complete an offer
* reward (int) - reward given for completing an offer
* duration (int) - time for offer to be open, in days
* channels (list of strings)

**profile.json**
* age (int) - age of the customer 
* became_member_on (int) - date when customer created an app account
* gender (str) - gender of the customer (note some entries contain 'O' for other rather than M or F)
* id (str) - customer id
* income (float) - customer's income

**transcript.json**
* event (str) - record description (ie transaction, offer received, offer viewed, etc.)
* person (str) - customer id
* time (int) - time in hours since start of test. The data begins at time t=0
* value - (dict of strings) - either an offer id or transaction amount depending on the record

# Project Definition

## Problem Statement

Based on the dataset provided by Starbucks, the aim of this project is to understand better the Starbucks offers, knowing which type of offer affects customers the most and providing more inteligence when sending or not a offer to the customer. Additionally, to make the goal more clear, the specific goals are depicted below:
* Create a data vizualization to understand how much each type of offer affect customers, using customers binned by profile
* Create a machine learning algorithm that tells if a offer will affect the customer or not

### Metrics
For the machine learning algorithm, the accuracy, recall, precision and F1-score will be used to understand how much the trained algorithm can be used to determine if Starbucks should or not send the offer.

### Notebook organization
1 - Import Data <br>
2 - Data Understanding <br>
3 - Data Cleaning <br>
4 - Data Vizualization <br>
5 - Offers Understanding <br>
6 - Modeling <br>

# Import Data

In [ ]:
import pandas as pd
import numpy as np
import math
import json
from tqdm import tqdm
import plotly.express as px
%matplotlib inline

# read in the json files
portfolio = pd.read_json('data/portfolio.json', orient='records', lines=True)
profile = pd.read_json('data/profile.json', orient='records', lines=True)
transcript = pd.read_json('data/transcript.json', orient='records', lines=True)

# Data Understanding

### Portfolio Dataset

In [ ]:
portfolio

Small dataset with some types of offers and difficulties/rewards related

### Profile Dataset

In [ ]:
profile

In [ ]:
profile.hist()

In [ ]:
px.histogram(profile, 'age')

In [ ]:
px.histogram(profile, 'income')

In [ ]:
px.histogram(profile, 'gender')

In [ ]:
profile.isnull().sum()

17000 persons dataset, with missing values for income and gender and some persons too old (> 100 years). Task to be cleaned in the next step

### Transcript Dataset

In [ ]:
transcript

In [ ]:
transcript['event'].value_counts()

In [ ]:
px.histogram(transcript, 'event')

In [ ]:
transcript['person'].value_counts()

Large dataset, with a lot of offers and transactions. Additionally, the persons with most interactions are about 51 interactions

# Data Pre-Processing

## Data Cleaning

In [ ]:
def clean_portfolio(portfolio):
    """
    Cleans the portfolio dataset renaming columns and applying one-hot enconding to the channels column
    INPUT:
    portfolio - (pandas dataframe) the portfolio dataset
    
    OUTPUT:
    portfolio - (pandas dataframe) the portfolio dataset cleaned
    """

    portfolio.rename(columns={'id': 'offer'}, inplace=True)
    for channel in ['email', 'mobile', 'social', 'web']:
        portfolio[channel] = portfolio['channels'].apply(lambda row: 1 if (channel in row) else 0)

    portfolio.drop(['channels'], axis=1, inplace=True)
    portfolio

    return portfolio

def clean_profile(profile):
    """
    Cleans the profile dataset removing rows without gender and income and persons too old
    INPUT:
    profile - (pandas dataframe) the portfolio dataset
    
    OUTPUT:
    profile - (pandas dataframe) the portfolio dataset cleaned
    real_persons - (list) a list containing all the real persons in the cleaned dataset
    """
    profile = profile[profile['income'].notnull()]
    profile = profile[profile['age'] <= 100]
    profile = profile[profile['gender'].notnull()]
    profile.rename(columns={'id': 'person'}, inplace=True)

    real_persons = profile['person'].unique()

    return profile, real_persons

def clean_transcript(transcript, real_persons):
    """
    Cleans the transcript dataset filtering by only real persons who received offers
    INPUT:
    transcript - (pandas dataframe) the portfolio dataset
    real_persons - (list) all unique and real persons returned from the profile dataset
    
    OUTPUT:
    transcript_offers - (pandas dataframe) the transcript with only people that had received offer from Starbucks
    """
    persons_received = transcript[transcript['event'] == 'offer received']['person'].unique()
    transcript_offers = transcript[transcript['person'].isin(persons_received)]
    transcript_offers = transcript_offers[transcript_offers['person'].isin(real_persons)]

    return transcript_offers

def create_offers_dataset(transcript_offers, real_persons):
    """
    Using the transcript_offers, creates a dataset with all the offers
    INPUT:
    transcript_offers - (pandas dataframe) the transcript_offers dataset cleaned and filtered
    real_persons - (list) all unique and real persons returned from the profile dataset
    
    OUTPUT:
    transcript_offers - (pandas dataframe) the transcript with only people that had received offer from Starbucks
    """

    # iterates to each person to create a dataset with the columns with times of received_offer, viewed_offer and completed_offer
    offers_df = pd.DataFrame()
    for person in tqdm(real_persons):
        df_aux = transcript_offers[transcript_offers['person'] == person]

        offers = dict()
        for line in range(len(df_aux)):
            if df_aux.iloc[line, df_aux.columns.get_loc('event')] == 'offer received':
                offers[df_aux.iloc[line, df_aux.columns.get_loc('value')].get('offer id')] = dict()
                offers[df_aux.iloc[line, df_aux.columns.get_loc('value')].get('offer id')]['person'] = person

                offers[df_aux.iloc[line, df_aux.columns.get_loc('value')].get('offer id')]['offer received time'] = df_aux.iloc[line, df_aux.columns.get_loc('time')]
            elif df_aux.iloc[line, df_aux.columns.get_loc('event')] == 'offer viewed':
                offers[df_aux.iloc[line, df_aux.columns.get_loc('value')].get('offer id')]['offer viewed time'] = df_aux.iloc[line, df_aux.columns.get_loc('time')]
            elif df_aux.iloc[line, df_aux.columns.get_loc('event')] == 'offer completed':
                offers[df_aux.iloc[line, df_aux.columns.get_loc('value')]['offer_id']]['offer completed time'] = df_aux.iloc[line, df_aux.columns.get_loc('time')]
                offers[df_aux.iloc[line, df_aux.columns.get_loc('value')]['offer_id']]['reward completed'] = df_aux.iloc[line, df_aux.columns.get_loc('value')]['reward']

        # merges the data
        offers_df = offers_df.append(pd.DataFrame(offers).transpose())


    offers_df['offer'] = offers_df.index

    return offers_df

def merge_offers_dataset(profile, portfolio, offers_df):
    """
    Merge the offers_df dataset with profile and portfolio information, including information about offers end time and success
    INPUT:
    profile - (pandas dataframe) the profile dataset cleaned
    portfolio - (pandas dataframe) the portfolio dataset cleaned
    offers_df - (pandas dataframe) the dataset formating offers with times
    
    OUTPUT:
    offers_df - (pandas dataframe) the dataset for offers with profile and offers information
    """
    offers_df = pd.merge(offers_df, profile, on=['person'], how='left')
    offers_df = pd.merge(offers_df, portfolio, on=['offer'], how='left')

    offers_df['offer end time'] = offers_df['offer received time'] + offers_df['duration']*24
    offers_df['offer success'] = (offers_df['offer completed time'] > offers_df['offer viewed time']).astype(int)
    offers_df['age bin'] = pd.cut(offers_df['age'], bins=5)
    offers_df['income_bin'] = pd.cut(offers_df['income'], bins=5).astype(str)

    return offers_df

def calculate_money_spent_in_offers(offers_df, transcript):
    """
    Calculates how much money is spent during an offer and updates the offer_df dataframe
    INPUT:
    offers_df - (pandas dataframe) the dataset for offers with profile and offers information
    transcript - (pandas dataframe) the transcript dataset cleaned and filtered
    
    OUTPUT:
    offers_df - (pandas dataframe) the dataset for offers with profile and offers information with money spent column added
    offers_transcript - (pandas dataframe) a dataset containing all money spent during offers time
    """

    offers_df['money spent in offer time'] = 0
    transcript_money = transcript[transcript['event'] == 'transaction']
    transcript_money = pd.concat([transcript_money, transcript_money['value'].apply(pd.Series)], axis=1)

    offers_transcript = pd.DataFrame()

    for line in tqdm(range(len(offers_df))):
        try:
            person = offers_df.iloc[line, offers_df.columns.get_loc('person')]
            time_begin_offer = offers_df.iloc[line, offers_df.columns.get_loc('offer received time')]
            time_end_offer = offers_df.iloc[line, offers_df.columns.get_loc('offer end time')]
            transcript_aux = transcript_money[(transcript_money['person'] == person) & (transcript_money['time'] >= time_begin_offer) & (transcript_money['time'] < time_end_offer)]

            offers_transcript = offers_transcript.append(transcript_aux)
            if not(transcript_aux.empty):
                offers_df.iloc[line, offers_df.columns.get_loc('money spent in offer time')] = transcript_aux['amount'].sum()
        except:
            print(offers_df.iloc[line])

    return offers_df, offers_transcript

Clean and merge datasets, creating an offer_df dataset with all offers and its result (success, fail). Additionally, a offers_transcript is created with all the transactions made during offers time

In [ ]:
portfolio = clean_portfolio(portfolio)
profile, real_persons = clean_profile(profile)
transcript_offers = clean_transcript(transcript, real_persons=real_persons)
offers_df = create_offers_dataset(transcript_offers=transcript_offers, real_persons=real_persons)
offers_df = merge_offers_dataset(profile, portfolio, offers_df)


In [35]:
offers_df, offers_transcript = calculate_money_spent_in_offers(offers_df=offers_df, transcript=transcript)

100%|██████████| 55204/55204 [20:49<00:00, 44.16it/s]


In [36]:
offers_df.describe()

age  became_member_on         income        reward  \
count  55204.000000      5.520400e+04   55204.000000  55204.000000   
mean      54.334758      2.016693e+07   65387.435693      4.205438   
std       17.375154      1.188918e+04   21626.543006      3.402472   
min       18.000000      2.013073e+07   30000.000000      0.000000   
25%       42.000000      2.016052e+07   49000.000000      2.000000   
50%       55.000000      2.017080e+07   63500.000000      5.000000   
75%       66.000000      2.017123e+07   80000.000000      5.000000   
max      100.000000      2.018073e+07  120000.000000     10.000000   

         difficulty      duration    email        mobile        social  \
count  55204.000000  55204.000000  55204.0  55204.000000  55204.000000   
mean       7.718770      6.508152      1.0      0.898812      0.599232   
std        5.547725      2.205497      0.0      0.301581      0.490059   
min        0.000000      3.000000      1.0      0.000000      0.000000   
25%        5.000000      5.000000      1.0      1.000000      0.000000   
50%       10.000000      7.000000      1.0      1.000000      1.000000   
75%       10.000000      7.000000      1.0      1.000000      1.000000   
max       20.000000     10.000000      1.0      1.000000      1.000000   

                web  offer success  money spent in offer time  
count  55204.000000   55204.000000               55204.000000  
mean       0.799308       0.298094                  29.801120  
std        0.400522       0.457425                  57.237229  
min        0.000000       0.000000                   0.000000  
25%        1.000000       0.000000                   1.950000  
50%        1.000000       0.000000                  15.720000  
75%        1.000000       1.000000                  39.140000  
max        1.000000       1.000000                1200.990000

In [38]:
offers_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 55204 entries, 0 to 55203
Data columns (total 23 columns):
 #   Column                     Non-Null Count  Dtype   
---  ------                     --------------  -----   
 0   person                     55204 non-null  object  
 1   offer received time        55204 non-null  object  
 2   offer completed time       27009 non-null  object  
 3   reward completed           27009 non-null  object  
 4   offer viewed time          41366 non-null  object  
 5   offer                      55204 non-null  object  
 6   gender                     55204 non-null  object  
 7   age                        55204 non-null  int64   
 8   became_member_on           55204 non-null  int64   
 9   income                     55204 non-null  float64 
 10  reward                     55204 non-null  int64   
 11  difficulty                 55204 non-null  int64   
 12  duration                   55204 non-null  int64   
 13  offer_type                 5520

In [37]:
offers_df.to_csv("processed_data/processed_offers.csv", index=False)
offers_transcript.to_csv("processed_data/offers_transcript.csv", index=False)

# Data Visualization

In [39]:
def plot_offers_funnel(offers_df):
    """
    Plots a funnel with the bogo, informational and discount offers, with the stages of received, viewed, completed and completed with success
    INPUT:
    offers_df - (pandas dataframe) the dataset for offers with profile and offers information and the offers result
    
    OUTPUT:
    (Plotly Express Funnel Figure) A Figure with the funnel for the 3 types of offer
    """

    stages = ["Offers Received", "Offers Viewed", "Offers Completed", "Offers Completed with Success"]

    df_bogo = pd.DataFrame(dict(number=[offers_df.loc[offers_df['offer_type'] == 'bogo','offer received time'].count(), 
                                        offers_df.loc[offers_df['offer_type'] == 'bogo', 'offer viewed time'].count(), 
                                        offers_df.loc[offers_df['offer_type'] == 'bogo', 'offer completed time'].count(),  
                                        offers_df.loc[offers_df['offer_type'] == 'bogo', 'offer success'].sum()], stage=stages))
    df_bogo['offer_type'] = 'bogo'

    df_informational = pd.DataFrame(dict(number=[offers_df.loc[offers_df['offer_type'] == 'informational','offer received time'].count(), 
                                                 offers_df.loc[offers_df['offer_type'] == 'informational', 'offer viewed time'].count(),
                                                 offers_df.loc[offers_df['offer_type'] == 'informational', 'offer completed time'].count(),  
                                                 offers_df.loc[offers_df['offer_type'] == 'informational', 'offer success'].sum()], stage=stages))
    df_informational['offer_type'] = 'informational'

    df_discount = pd.DataFrame(dict(number=[offers_df.loc[offers_df['offer_type'] == 'discount','offer received time'].count(), 
                                            offers_df.loc[offers_df['offer_type'] == 'discount', 'offer viewed time'].count(), 
                                            offers_df.loc[offers_df['offer_type'] == 'discount', 'offer completed time'].count(),  
                                            offers_df.loc[offers_df['offer_type'] == 'discount', 'offer success'].sum()], stage=stages))
    df_discount['offer_type'] = 'discount'

    data = pd.concat([df_bogo, df_discount, df_informational], axis=0)
    return px.funnel(data, x='number', y='stage', color='offer_type')

In [47]:
offers_df = pd.read_csv("processed_data/processed_offers.csv")
offers_transcript = pd.read_csv("processed_data/offers_transcript.csv")

In [48]:
px.histogram(offers_df, x="gender")

In [49]:
px.histogram(offers_df, x="age bin")

In [50]:
px.histogram(offers_df, x="offer_type")

In [44]:
plot_offers_funnel(offers_df=offers_df)

In [51]:
px.histogram(offers_df, x="income_bin")

In [52]:
px.treemap(offers_df, path=['offer_type', 'income_bin', 'gender'], values='offer success')

# Offers Understanding

## Revenue difference based on the offers

In [ ]:
offers_profile_transcript = pd.merge(offers_transcript, profile, on=['person'], how='left')
offers_profile_transcript['age bin'] = pd.cut(offers_profile_transcript['age'], bins=5)
offers_profile_transcript['income bin'] = pd.cut(offers_profile_transcript['income'], bins=5).astype(str)

non_offers_transcript = pd.concat([transcript_money.drop('value', axis=1),offers_transcript]).drop_duplicates(keep=False)
non_offers_transcript_profile = pd.merge(non_offers_transcript, profile, on=['person'], how='left')
non_offers_transcript_profile['age bin'] = pd.cut(non_offers_transcript_profile['age'], bins=5)
non_offers_transcript_profile['income'] = pd.cut(non_offers_transcript_profile['income'], bins=5).astype(str)

non_offers_summary = non_offers_transcript_profile.groupby(['income', 'gender']).mean()
offers_summary = offers_profile_transcript.groupby(['income bin', 'gender']).mean()

In [ ]:
bogo_offers_summary = offers_profile_complete[offers_profile_complete['offer_type'] == 'bogo'].groupby(['income_bin', 'gender']).mean()
discount_offers_summary = offers_profile_complete[offers_profile_complete['offer_type'] == 'discount'].groupby(['income_bin', 'gender']).mean()

In [ ]:
offers_summary.rename(columns={'amount': 'amount offer'}, inplace=True)
non_offers_summary.rename(columns={'amount': 'amount non offers'}, inplace=True)
discount_offers_summary.rename(columns={'offer success': 'discount offer success'}, inplace=True)
bogo_offers_summary.rename(columns={'offer success': 'bogo offer success'}, inplace=True)

In [ ]:
difference_offer_non_offer = pd.concat([offers_summary, non_offers_summary, discount_offers_summary, bogo_offers_summary], axis=1)[['amount offer', 'amount non offers', 'discount offer success', 'bogo offer success']]
difference_offer_non_offer['profit ratio'] = difference_offer_non_offer['amount offer']/difference_offer_non_offer['amount non offers']
difference_offer_non_offer

In [ ]:
difference_offer_non_offer.describe().loc['mean']

In [ ]:
fig = px.bar(difference_offer_non_offer, x=offers_summary.index.get_level_values(0), y='profit ratio', color=offers_summary.index.get_level_values(1), title='Profit Ratio', barmode='group')
fig.show()

In [ ]:
fig = px.bar(difference, x=offers_summary.index.get_level_values(0), y='discount offer success', color=offers_summary.index.get_level_values(1), title='Discount success ratio', barmode='group')
fig.update_yaxes(range=[0,1])

In [ ]:
fig = px.bar(difference, x=offers_summary.index.get_level_values(0), y='bogo offer success', color=offers_summary.index.get_level_values(1), title='Bogo success ratio', barmode='group')
fig.update_yaxes(range=[0,1])

### Completed offers

In [ ]:
bogo_offers_summary = offers_profile_complete[offers_profile_complete['offer_type'] == 'bogo'].groupby(['income_bin', 'gender', 'age bin']).mean()
discount_offers_summary = offers_profile_complete[offers_profile_complete['offer_type'] == 'discount'].groupby(['income_bin', 'gender', 'age bin']).mean()

#### Bogo

In [ ]:
fig = px.scatter(bogo_offers_summary, x='income', y='offer success', color=bogo_offers_summary.index.get_level_values(1), size='age', title='Bogo sucess average by income', trendline="ols")
fig.update_yaxes(range=[0,1])

#### Discount

In [ ]:
fig = px.scatter(discount_offers_summary, x='income', y='offer success', color=discount_offers_summary.index.get_level_values(1), size='age', title='Discount sucess average by income', trendline="ols")
fig.update_yaxes(range=[0,1])

#### Informational

In [ ]:
offers_profile_complete['viewed success'] = (offers_profile_complete['offer viewed time'] >= offers_profile_complete['offer received time']).astype(int)
offers_profile_complete

In [ ]:
info_offers_summary = offers_profile_complete[offers_profile_complete['offer_type'] == 'informational'].groupby(['income_bin', 'gender']).mean()

In [ ]:
px.bar(info_offers_summary, x=info_offers_summary.index.get_level_values(0), y='viewed success', color=info_offers_summary.index.get_level_values(1), barmode='group', title='Informational view success average by income')

In [ ]:
offers_profile_complete

In [ ]:
informational_dataset_success = offers_profile_complete[(offers_profile_complete['offer_type'] == 'informational') & (offers_profile_complete['viewed success'] == 1)]
informational_dataset_success = informational_dataset_success.groupby(['income_bin', 'gender']).mean()
informational_dataset_success.rename(columns={'money spent in offer time': 'money spent in offer time - informational'}, inplace=True)

informational_dataset_failure = offers_profile_complete[(offers_profile_complete['offer_type'] == 'informational') & (offers_profile_complete['viewed success'] == 0)]
informational_dataset_failure = informational_dataset_failure.groupby(['income_bin', 'gender']).mean()
informational_dataset_failure.rename(columns={'money spent in offer time': 'money spent in offer time - non-offer'}, inplace=True)

In [ ]:
comparison_informational = pd.concat([informational_dataset_success, informational_dataset_failure], axis=1)[['money spent in offer time - informational', 'money spent in offer time - non-offer']]
comparison_informational['ratio'] = comparison_informational['money spent in offer time - informational']/comparison_informational['money spent in offer time - non-offer']
comparison_informational

In [ ]:
px.bar(comparison_informational, x=comparison_informational.index.get_level_values(0), y='ratio', color=comparison_informational.index.get_level_values(1), barmode='group', title='Profit ratio influenced by the informational')

# Prediction tool for offer success

In [ ]:
from pycaret.classification import * 
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report

In [ ]:
dataset = offers_profile_complete[['gender', 'age', 'income', 'reward', 'difficulty', 'duration', 'offer_type', 'email', 'mobile', 'social', 'web', 'offer success']]

In [ ]:
train, blind_test = train_test_split(dataset, test_size=0.1, shuffle=True)

In [ ]:
train

In [ ]:
clf = setup(train, target = 'offer success', use_gpu=True)

In [ ]:
best = compare_models(sort='F1')

In [ ]:
gbc = create_model('lda')
best = tune_model(gbc, n_iter=10)

In [ ]:
save_model(best, 'models/lda')

In [ ]:
interpret_model(best)

In [ ]:
y_pred = predict_model(best, data=blind_test[['gender', 'age', 'income', 'reward', 'difficulty', 'duration', 'offer_type', 'email', 'mobile', 'social', 'web']])

In [ ]:
y_pred['real'] = blind_test['offer success']
y_pred

In [ ]:
confusion_matrix(blind_test['offer success'], y_pred['Label'])

In [ ]:
print(classification_report(blind_test['offer success'], y_pred['Label']))